In [ ]:
from selenium import webdriver
from selenium.webdriver.common.by import By
from selenium.webdriver.chrome.service import Service
from selenium.webdriver.chrome.options import Options
import time
from fake_useragent import UserAgent
import random
import pandas as pd
from selenium.webdriver.support.ui import WebDriverWait
from selenium.webdriver.support import expected_conditions as EC
from selenium.common.exceptions import NoSuchElementException

ua = UserAgent()
user_agents = [
    "Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/94.0.4606.61 Safari/537.36",
    "Mozilla/5.0 (Windows NT 10.0; Win64; x64; rv:93.0) Gecko/20100101 Firefox/93.0",
]

# Configure Chrome options
options = Options()
# options.add_argument("--headless")  # Run headless for no GUI
# options.add_argument("--no-sandbox")
# options.add_argument("--disable-dev-shm-usage")
options.add_argument(f"user-agent={random.choice(user_agents)}")


# Navigate to the URL
url = "https://www.otodom.pl/pl/wyniki/sprzedaz/mieszkanie/opolskie/nyski/lambinowice/lambinowice?distanceRadius={}&viewType=listing&page="
# url = "https://www.otodom.pl/pl/wyniki/sprzedaz/mieszkanie/dolnoslaskie/wroclaw/wroclaw/wroclaw?distanceRadius={}&viewType=listing&page="
distance = 25
print(url.format(distance))


apartment_columns = ['URL', 'Title', 'Price', 'PpSM', #Basic info
                    'Street', 'Subdistrict', 'City District', 'City', 'Commune', 'District', 'Voivodeship', #Address
                    'Area', 'Rooms', 'Heating', 'Floor', 'Rent', 'Condition', 'Market', 'Form of Ownership', 'Availability', 'Seller Type', 'Additional Information', #Details
                    'Year', 'Elevator', 'Type of Development', 'Building Material', 'Windows', 'Energy Certificate', 'Safety', #Building and materials
                    'Security', 'Media', 'Equipment', #Equipment
                    'Description']

apartment_details_mapping = {
    'Ogrzewanie' : 'Heating',
    'Piętro' : 'Floor',
    'Czynsz' : 'Rent',
    'Stan wykończenia' : 'Condition',
    'Rynek' : 'Market',
    'Forma własności' : 'Form of Ownership',
    'Dostępne od' : 'Availability',
    'Typ ogłoszeniodawcy' : 'Seller Type',
    'Informacje dodatkowe' : 'Additional Information',
    'Rok Budowy' : 'Year',
    'Winda' : 'Elevator',
    'Rodzaj zabudowy' : 'Type of Development',
    'Materiał budynku' : 'Building Material',
    'Okna' : 'Windows',
    'Certyfikat energetyczny' : 'Energy Certificate',
    'Bezpieczeństwo' : 'Safety',
    'Wyposażenie' : 'Equipment',
    'Zabezpieczenia' : 'Security'
}

https://www.otodom.pl/pl/wyniki/sprzedaz/mieszkanie/opolskie/nyski/lambinowice/lambinowice?distanceRadius=5&viewType=listing&page=


In [ ]:
def number_of_pages(driver:webdriver.Chrome):
    try:
        page_list = driver.find_elements(By.CLASS_NAME, 'css-43nhzf')
        return(max([int(pg.text) for pg in page_list]))
    except Exception as e:
        print(e)
        return 1

def split_address(full_address):
    ### Figure out splitting adifferent addresses
    # os. Zacisze, Kopice, Grodków, brzeski, opolskie
    # ul. Zwycięska 3, Partynice, Krzyki, Wrocław, dolnośląskie
    # ul. Obozowa, Łambinowice, Łambinowice, nyski, opolskie
    address_list = [part.strip() for part in full_address.split(',')]
    voivodeship = address_list[-1]
    address = {'Voivodeship' : voivodeship}
    if len(address_list) == 5:
        street = address_list[0]
    else:
        street = ''
        
    if address_list[-2][-3:] in ('ski', 'cki'):
        district = address_list[-2]
        commune = address_list[-3]
        city = address_list[-4]
        address.update({'District' : district, 'Commune' : commune, 'City' : city, 'City District' : None, 'Subdistrict' : None})
    else:
        city = address_list[-2]
        city_district = address_list[-3]
        subdistrict = address_list[-4]
        address.update({'District' : None, 'Commune' : None, 'City' : city, 'City District' : city_district, 'Subdistrict' : subdistrict})
        
    address['Street'] = street
    return address

In [5]:

# Set up the Chrome WebDriver
driver = webdriver.Chrome(options=options)
driver.get(url.format(distance))

# Wait for the page to load
time.sleep(1)

max_page = number_of_pages(driver)
print(f'Number of pages {max_page}')

df = pd.DataFrame(columns=apartment_columns)

internal_index = 1
for page in range(1, max_page+1):
    print(f'Page Number {page}')
    
    # Get all listings from page
    listings = driver.find_elements(By.CSS_SELECTOR, 'div[data-cy="search.listing.organic"] a[data-cy="listing-item-link"]')
    print(f'Listings {len(listings)}')
    # Loop through each listing and click
    for listing in listings:
        print(internal_index)
        # Open the link in a new tab for listing
        listing_link = listing.get_attribute("href")
        driver.execute_script("window.open(arguments[0]);", listing_link)
        driver.switch_to.window(driver.window_handles[-1])
        print(listing_link)
        listing_info = {'URL' : listing_link}
        # Wait for the new page to load
        time.sleep(0.1)  
        
        # Get listing details
        title = driver.find_element(By.CLASS_NAME , 'css-wqvm7k').text
        price = driver.find_element(By.CLASS_NAME , 'css-1o51x5a').text # 1ftqasz
        if price == 'Zapytaj o cenę':
            price = None
        try:
            ppsm = driver.find_element(By.CLASS_NAME , 'css-z3xj2a').text
        except NoSuchElementException:
            ppsm = None
        address = driver.find_element(By.CLASS_NAME , 'css-1jjm9oe').text
        address_dict = split_address(address)
        listing_info.update(address_dict)
        
        area_rooms = driver.find_elements(By.CLASS_NAME , 'css-1ftqasz')
        area = area_rooms[0].text
        rooms = area_rooms[1].text
        listing_info.update({'Title' : title, 'Price' : price, 'PpSM' : ppsm, 'Area' : area, 'Rooms' : rooms})
        # basic_info = {'Title' : title, 'Price' : price, 'PpSM' : ppsm, 'Area' : area, 'Rooms' : rooms}
        # Scroll to an end of the page to load everything
        driver.execute_script("window.scrollTo(0, document.body.scrollHeight);")
        # print(basic_info)
        # Open all hidden elements
        elements = driver.find_elements(By.CLASS_NAME, "css-1g1u77j")
        for element in elements:
            driver.execute_script("arguments[0].click();", element)
        
        
        details = driver.find_elements(By.CLASS_NAME , 'css-1airkmu')
        details = [detail.text for detail in details]
        
        # Add empty string if no value for key
        i = 0
        while i < len(details):
            if ":" in details[i] and (i + 1 == len(details) or ":" in details[i + 1]):
                details.insert(i + 1, ' ')
                i += 1  # Skip the inserted element to avoid infinite loop
            i += 1   
            
        # Remove unwanted characters
        details = [
            detail.replace(':', '').strip().split('\n') if '\n' in detail else detail.replace(':', '').strip()
            for detail in details]
        
        details = dict(zip(details[::2], details[1::2]))
        mapped_dict = {apartment_details_mapping[key] if key in apartment_details_mapping else key : value for key, value in details.items()} 
        # print(details)
        for key in details.keys():
            if key not in apartment_details_mapping.keys():
                print(key)
        # print(mapped_dict)
        listing_info.update(mapped_dict)
        time.sleep(2)
        
        print(title, price, ppsm)
        print(address_dict)
        # Close the tab and return to the main tab
        driver.close()
        driver.switch_to.window(driver.window_handles[0])
        internal_index += 1
        df.loc[len(df)] = listing_info
        print(df)
    # if page == max_page:
    #     break
    driver.get(url.format(distance) + f'{page+1}')
    time.sleep(10)

time.sleep(1)
# Close the driver
driver.quit()

max() iterable argument is empty
Number of pages 1
Page Number 1
Listings 3
1
https://www.otodom.pl/pl/oferta/sprzedam-mieszkanie-w-lambinowicach-ID4poTT
Media
Sprzedam mieszkanie w Łambinowicach 245 000 zł 4 804 zł/m²
{'Voivodeship': 'opolskie', 'District': 'nyski', 'Commune': 'Łambinowice', 'City': 'Łambinowice', 'City District': None, 'Subdistrict': None, 'Street': 'ul. Obozowa'}
                                                 URL  \
0  https://www.otodom.pl/pl/oferta/sprzedam-miesz...   

                                 Title       Price         PpSM       Street  \
0  Sprzedam mieszkanie w Łambinowicach  245 000 zł  4 804 zł/m²  ul. Obozowa   

  Subdistrict City District         City      Commune District  ... Elevator  \
0        None          None  Łambinowice  Łambinowice    nyski  ...      nie   

  Type of Development Building Material    Windows  \
0                blok               NaN  drewniane   

                 Energy Certificate Safety            Security  \
0  W

In [53]:
from selenium import webdriver
from selenium.webdriver.common.by import By
from selenium.webdriver.chrome.service import Service
from selenium.webdriver.chrome.options import Options
import time
from fake_useragent import UserAgent
import random
import pandas as pd
from selenium.webdriver.support.ui import WebDriverWait
from selenium.webdriver.support import expected_conditions as EC
from selenium.common.exceptions import NoSuchElementException

ua = UserAgent()
user_agents = [
    "Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/94.0.4606.61 Safari/537.36",
    "Mozilla/5.0 (Windows NT 10.0; Win64; x64; rv:93.0) Gecko/20100101 Firefox/93.0",
]

# Configure Chrome options
options = Options()
# options.add_argument("--headless")  # Run headless for no GUI
# options.add_argument("--no-sandbox")
# options.add_argument("--disable-dev-shm-usage")
options.add_argument(f"user-agent={random.choice(user_agents)}")

# Set up the Chrome WebDriver
driver = webdriver.Chrome(options=options)

# Navigate to the URL
url = "https://www.otodom.pl/pl/wyniki/sprzedaz/mieszkanie/opolskie/nyski/lambinowice/lambinowice?distanceRadius={}&viewType=listing&page="
# url = "https://www.otodom.pl/pl/wyniki/sprzedaz/mieszkanie/dolnoslaskie/wroclaw/wroclaw/wroclaw?distanceRadius={}&viewType=listing&page="
distance = 100
print(url.format(distance))
driver.get(url.format(distance))

# Wait for the page to load
time.sleep(1)

def number_of_pages(driver:webdriver.Chrome):
    try:
        page_list = driver.find_elements(By.CLASS_NAME, 'css-43nhzf')
        return(max([int(pg.text) for pg in page_list]))
    except Exception as e:
        print(e)
        return 1

def split_address(full_address):
    ### Figure out splitting adifferent addresses
    # os. Zacisze, Kopice, Grodków, brzeski, opolskie
    # ul. Zwycięska 3, Partynice, Krzyki, Wrocław, dolnośląskie
    # ul. Obozowa, Łambinowice, Łambinowice, nyski, opolskie
    address_list = [part.strip() for part in full_address.split(',')]
    voivodeship = address_list[-1]
    address = {'Voivodeship' : voivodeship}
    if len(address_list) == 5:
        street = address_list[0]
    else:
        street = ''
    if len(address_list) == 3:
        city = address_list[0]
        district = address_list[1]
        address.update({'District' : district, 'Commune' : None, 'City' : city, 'City District' : None, 'Subdistrict' : None, 'Street' : street})
        return address
        
    if address_list[-2][-3:] in ('ski', 'cki'):
        district = address_list[-2]
        commune = address_list[-3]
        city = address_list[-4]
        address.update({'District' : district, 'Commune' : commune, 'City' : city, 'City District' : None, 'Subdistrict' : None})
    else:
        city = address_list[-2]
        city_district = address_list[-3]
        subdistrict = address_list[-4]
        address.update({'District' : None, 'Commune' : None, 'City' : city, 'City District' : city_district, 'Subdistrict' : subdistrict})
        
    address['Street'] = street
    return address

def split_and_map(elements, map_dict):
    if not isinstance(elements, list):
        elements = [elements]
    # print(elements)
    elements = {map_dict[el] if el in map_dict else el : True for el in elements}
    # print(elements)
    return elements

max_page = number_of_pages(driver)
print(f'Number of pages {max_page}')

apartment_columns = ['URL', 'ID', 'Title', 'Price', 'PpSM', #Basic info
                    'Street', 'Subdistrict', 'City District', 'City', 'Commune', 'District', 'Voivodeship', #Address
                    'Area', 'Rooms', 'Heating', 'Floor', 'Rent', 'Condition', 'Market', 'Form of Ownership', 'Availability', 'Seller Type', 'Additional Information', #Details
                    'Balcony', 'Basement', 'Air Conditioning', 'Utility Room', 'Garden', 'Garage/Parking Space', 'Terrace', 'Separate Kitchen' #Additional Information
                    'Year', 'Elevator', 'Type of Development', 'Building Material', 'Windows', 'Energy Certificate', 'Safety', #Building and materials
                    'Anti-burglary Blinds', 'Anti-burglary Doors/Windows', 'Intercom/Videophone', 'Alarm system', 'Gated Community' #Security
                    'Furniture', 'Refigerator', 'TV', 'Washing Machine', 'Stove', 'Dishwasher', 'Oven' #Equipment
                    'Internet', 'Cable TV', 'Landline' #Media
                    'Description']
df = pd.DataFrame(columns=apartment_columns)


apartment_details_mapping = {
    'Ogrzewanie' : 'Heating',
    'Piętro' : 'Floor',
    'Czynsz' : 'Rent',
    'Stan wykończenia' : 'Condition',
    'Rynek' : 'Market',
    'Forma własności' : 'Form of Ownership',
    'Dostępne od' : 'Availability',
    'Typ ogłoszeniodawcy' : 'Seller Type',
    'Informacje dodatkowe' : 'Additional Information',
    'Rok budowy' : 'Year',
    'Winda' : 'Elevator',
    'Rodzaj zabudowy' : 'Type of Development',
    'Materiał budynku' : 'Building Material',
    'Okna' : 'Windows',
    'Certyfikat energetyczny' : 'Energy Certificate',
    'Bezpieczeństwo' : 'Safety',
    'Wyposażenie' : 'Equipment',
    'Zabezpieczenia' : 'Security'
}

equipment_mapping = {
    'Meble' : 'Furniture',
    'Lodówka' : 'Refigerator',
    'Telewizor' : 'TV',
    'Pralka' : 'Washing Machine',
    'Kuchenka' : 'Stove',
    'Zmywarka' : 'Dishwasher',
    'Piekarnik' : 'Oven'
}

media_mapping = {
    'internet' : 'Internet',
    'telewizja kablowa' : 'Cable TV',
    'telefon' : 'Landline'
}

additional_information_mapping = {
    'balkon' : 'Balcony',
    'piwnica' : 'Basement',
    'klimatyzacja' : 'Air Conditioning',
    'pom. użytkowe' : 'Utility Room',
    'ogródek' : 'Garden',
    'garaż/miejsce parkingowe' : 'Garage/Parking Space',
    'taras' : 'Terrace',
    'oddzielna kuchnia' : 'Separate kitchen'
}

security_mapping = {
    'rolety antywłamaniowe' : 'Anti-burglary Blinds',
    'drzwi / okna antywłamaniowe' : 'Anti-burglary Doors/Windows',
    'domofon / wideofon' : 'Intercom/Videophone',
    'monitoring / ochrona' : 'Monitoring/Security',
    'system alarmowy' : 'Alarm System',
    'teren zamknięty' : 'Gated Community'
}

not_found = set()
adres = {}
internal_index = 1
for page in range(1, max_page+1):
    print(f'Page Number {page}')
    
    # Get all listings from page
    listings = driver.find_elements(By.CSS_SELECTOR, 'div[data-cy="search.listing.organic"] a[data-cy="listing-item-link"]')
    print(f'Listings {len(listings)}')
    # Loop through each listing and click
    for listing in listings:
        print(internal_index)
        # Open the link in a new tab for listing
        listing_link = listing.get_attribute("href")
        driver.execute_script("window.open(arguments[0]);", listing_link)
        driver.switch_to.window(driver.window_handles[-1])
        print(listing_link)
        listing_info = {'URL' : listing_link, 'ID' : listing_link.split('-')[-1]}
        # Wait for the new page to load
        time.sleep(0.1)  
        
        # Get listing details
        title = driver.find_element(By.CLASS_NAME , 'css-wqvm7k').text
        price = driver.find_element(By.CLASS_NAME , 'css-1o51x5a').text # 1ftqasz
        if price == 'Zapytaj o cenę':
            price = None
            
        try:
            ppsm = driver.find_element(By.CLASS_NAME , 'css-z3xj2a').text
        except NoSuchElementException:
            ppsm = None
            
        listing_info.update({'Title' : title, 'Price' : price, 'PpSM' : ppsm})
            
        address = driver.find_element(By.CLASS_NAME , 'css-1jjm9oe').text
        address_dict = split_address(address)
        listing_info.update(address_dict)
        adres[address] = address_dict
        area_rooms = [el.text for el in driver.find_elements(By.CLASS_NAME , 'css-1ftqasz')]
        for el in area_rooms:
            if 'm²' in el:
                listing_info.update({'Area' : el})
            elif el[:3] == 'pok':
                listing_info.update({'Rooms' : el})
            else:
                listing_info.update({'Two-story' : True})
        # area = area_rooms[0].text
        # rooms = area_rooms[1].text
        #area_roms[2] == 'dwupoziomowe'
        #  'Area' : area, 'Rooms' : rooms})
        # basic_info = {'Title' : title, 'Price' : price, 'PpSM' : ppsm, 'Area' : area, 'Rooms' : rooms}
        
        # Scroll to an end of the page to load everything
        driver.execute_script("window.scrollTo(0, document.body.scrollHeight);")
        # print(basic_info)
        # Open all hidden elements
        elements = driver.find_elements(By.CLASS_NAME, "css-1g1u77j")
        for element in elements:
            driver.execute_script("arguments[0].click();", element)
        
        
        details = driver.find_elements(By.CLASS_NAME , 'css-1airkmu')
        details = [detail.text for detail in details]
        
        # Add empty string if no value for key
        i = 0
        while i < len(details):
            if ":" in details[i] and (i + 1 == len(details) or ":" in details[i + 1]):
                details.insert(i + 1, ' ')
                i += 1  # Skip the inserted element to avoid infinite loop
            i += 1   
            
        # Remove unwanted characters
        details = [
            detail.replace(':', '').strip().split('\n') if '\n' in detail else detail.replace(':', '').strip()
            for detail in details]
        print(details)
        details = dict(zip(details[::2], details[1::2]))
        mapped_dict = {apartment_details_mapping[key] if key in apartment_details_mapping else key : value for key, value in details.items()} 
        print(mapped_dict)
        
        # split list of 'Additional Information' into columns and map to english
        
        additional_information_dict = mapped_dict.pop('Additional Information', [])
        additional_information_dict = split_and_map(additional_information_dict, additional_information_mapping)
        
        # split list of Media into columns
        media_dict = mapped_dict.pop('Media', [])
        media_dict = split_and_map(media_dict, media_mapping)
        
        # split list of Equipment into columns
        equipment_dict = mapped_dict.pop('Equipment', [])
        equipment_dict = split_and_map(equipment_dict, equipment_mapping)
        
        # split list of Security into columns
        security_dict = mapped_dict.pop('Security', [])
        security_dict = split_and_map(security_dict, security_mapping)
                
        # print(mapped_dict)
        # print(additional_information_dict)
        # print(media_dict)
        # print(equipment_dict)
        # print(security_dict)
        # print(details)
        for key in details.keys():
            if key not in apartment_details_mapping.keys():
                not_found.add(key)
        # print(mapped_dict)
        listing_info.update(mapped_dict)
        listing_info.update(additional_information_dict)
        listing_info.update(media_dict)
        listing_info.update(equipment_dict)
        listing_info.update(security_dict)
        time.sleep(0.5)
        
        print(title, price, ppsm)
        print(address_dict)
        # Close the tab and return to the main tab
        driver.close()
        driver.switch_to.window(driver.window_handles[0])
        internal_index += 1
        df.loc[len(df)] = listing_info
        # print(df)
    if page != max_page:
        # break
        driver.get(url.format(distance) + f'{page+1}')
        time.sleep(10)

print(df)
time.sleep(1)
# Close the driver
driver.quit()

# Print the extracted data
# for house in houses:
    # print(house)

https://www.otodom.pl/pl/wyniki/sprzedaz/mieszkanie/opolskie/nyski/lambinowice/lambinowice?distanceRadius=100&viewType=listing&page=
Number of pages 543
Page Number 1
Listings 20
1
https://www.otodom.pl/pl/oferta/wygodne-3p-z-balkonem-miejscem-i-komorka-ID4tU2w
['Ogrzewanie', '', 'Piętro', '2/4', 'Czynsz', '730 zł', 'Stan wykończenia', 'do zamieszkania', 'Rynek', 'wtórny', 'Forma własności', 'pełna własność', 'Dostępne od', '', 'Typ ogłoszeniodawcy', 'biuro nieruchomości', 'Informacje dodatkowe', ['balkon', 'garaż/miejsce parkingowe', 'pom. użytkowe'], 'Rok budowy', '2022', 'Winda', 'nie', 'Wyposażenie', ['piekarnik', 'lodówka', 'pralka', 'zmywarka']]
{'Heating': '', 'Floor': '2/4', 'Rent': '730 zł', 'Condition': 'do zamieszkania', 'Market': 'wtórny', 'Form of Ownership': 'pełna własność', 'Availability': '', 'Seller Type': 'biuro nieruchomości', 'Additional Information': ['balkon', 'garaż/miejsce parkingowe', 'pom. użytkowe'], 'Year': '2022', 'Elevator': 'nie', 'Equipment': ['piekarni

WebDriverException: Message: disconnected: not connected to DevTools
  (failed to check if window was closed: disconnected: not connected to DevTools)
  (Session info: chrome=131.0.6778.140)
Stacktrace:
	GetHandleVerifier [0x00007FF764596CC5+28821]
	(No symbol) [0x00007FF764503850]
	(No symbol) [0x00007FF7643A578A]
	(No symbol) [0x00007FF764390866]
	(No symbol) [0x00007FF764391D1F]
	(No symbol) [0x00007FF7643A5DD3]
	(No symbol) [0x00007FF76437EFCD]
	(No symbol) [0x00007FF76442D699]
	(No symbol) [0x00007FF76441F2C0]
	(No symbol) [0x00007FF7643EA778]
	(No symbol) [0x00007FF7643EB8E1]
	GetHandleVerifier [0x00007FF7648CFCCD+3408029]
	GetHandleVerifier [0x00007FF7648E743F+3504143]
	GetHandleVerifier [0x00007FF7648DB61D+3455469]
	GetHandleVerifier [0x00007FF76465BDCB+835995]
	(No symbol) [0x00007FF76450EB6F]
	(No symbol) [0x00007FF76450A824]
	(No symbol) [0x00007FF76450A9BD]
	(No symbol) [0x00007FF7644FA1A9]
	BaseThreadInitThunk [0x00007FFBF020259D+29]
	RtlUserThreadStart [0x00007FFBF1CEAF38

In [54]:
not_found

{'', 'Media'}

In [36]:
pd.set_option('display.max_columns', None)  # Show all columns
pd.set_option('display.max_colwidth', None)  # Show full column content
pd.set_option('display.expand_frame_repr', False)  # Prevent wrapping to new lines
df

URL        ID                                               Title       Price         PpSM                 Street Subdistrict City District          City      Commune District Voivodeship     Area  Rooms        Heating     Floor    Rent        Condition     Market Form of Ownership Availability          Seller Type  Additional Information Balcony Basement  Air Conditioning Utility Room Garden Garage/Parking Space Terrace  Separate KitchenYear Elevator Type of Development Building Material     Windows                Energy Certificate  Safety  Anti-burglary Blinds  Anti-burglary Doors/Windows  Intercom/Videophone  Alarm system  Gated CommunityFurniture  Refigerator  TV  Washing Machine  Stove  Dishwasher  OvenInternet Cable TV  LandlineDescription
0       https://www.otodom.pl/pl/oferta/dwupokojowe-mieszkanie-w-graczach-bezczynszowe-ID4tTUs   ID4tTUs    Dwupokojowe mieszkanie w Graczach - bezczynszowe  177 000 zł  3 491 zł/m²                               None          None        Gracze    Niemodlin  opolski    opolskie   50.7m²    NaN           inne       1/2               do remontu     wtórny    pełna własność   2024-12-13  biuro nieruchomości                     NaN     1.0      1.0               NaN          NaN    1.0                  NaN     NaN                   NaN      nie                 NaN               NaN         NaN                               NaN     NaN                   NaN                          NaN                  NaN           NaN                       NaN          NaN NaN              NaN    NaN         NaN           NaN      NaN                  NaN
1       https://www.otodom.pl/pl/oferta/mieszkanie-sprzedaz-3-pok-77m2-garaz-niemodlin-ID4rOUh   ID4rOUh    Mieszkanie sprzedaż 3 pok 77m2, garaż, Niemodlin  349 000 zł  4 503 zł/m²                               None          None     Niemodlin    Niemodlin  opolski    opolskie   77.5m²    NaN         gazowe       1/1    0 zł                      wtórny    pełna własność               biuro nieruchomości                     NaN     1.0      1.0               NaN          NaN    NaN                  1.0     NaN                   NaN      nie           kamienica               NaN  plastikowe                               NaN     NaN                   NaN                          NaN                  NaN           NaN                       NaN          NaN NaN              NaN    NaN         NaN           NaN      NaN                  NaN
2                       https://www.otodom.pl/pl/oferta/mieszkanie-2-pokojowe-lasocice-ID4tKaJ   ID4tKaJ                    Mieszkanie 2 pokojowe - Lasocice  165 000 zł  3 056 zł/m²                               None          None      Lasocice  Łambinowice    nyski    opolskie     54m²    NaN      kotłownia       1/2    0 zł  do zamieszkania     wtórny                                 biuro nieruchomości                     NaN     NaN      1.0               NaN          NaN   True                 True     NaN                   NaN      nie                blok               NaN  plastikowe                               NaN     NaN                   NaN                          NaN                  NaN           NaN                       NaN          NaN NaN              NaN    NaN         NaN           NaN      NaN                  NaN
3                             https://www.otodom.pl/pl/oferta/mieszkanie-w-korfantowie-ID4qo0A   ID4qo0A                            Mieszkanie w Korfantowie  229 000 zł  6 543 zł/m²         ul. Wyzwolenia        None          None     Korfantów    Korfantów    nyski    opolskie     35m²    NaN    elektryczne       2/2  200 zł  do zamieszkania     wtórny    pełna własność   2024-10-02             prywatny                     NaN     NaN      NaN               NaN          NaN    NaN                  NaN     NaN                   NaN      nie           kamienica             cegła  plastikowe  W trakcie realizacji / Zwolnione     NaN                   NaN                          NaN          